# Synthesis Planning
This notebook goes through the whole process to use the optimized model and produce the synthesis planning.

## Environment Setup
First of all, we need to make sure that the notebook is running in the correct environment.

To do that, follow these steps:
 1. Create the project's environment
    To do that, place yourself in the project's root, and run :
    `conda env create -f environment.yml`
    This creates a new clean conda environment with the package needed by the project.
 2. Activate the environment
    On Linux and Mac:
    `source activate synnet`
    On Windows:
    `conda activate synnet`
 3. Install the project's module
    Now that the environment is activated, we need to install the project as a module.
    Place yourself in the project's root and run :
    `pip install -e .`
 4. Restart Jupyter from the new environment
    Now, we can start Jupyter from the environment, that way it has all the dependencies we need. Simply run `jupyter notebook` and open this notebook.

To test the setup, run the following cell.

In [2]:
import sys

# Check that the correct conda env is being used
if sys.prefix.split("/")[-1] != "synnet": #I have changed the split symbol from ("\\") to ("/") because it was giving some problems.
    print("You are not using the correct conda environment, please follow the instructions above")
else:
    try:
        import synnet

        print("The environment is setup correctly")
    except ImportError:
        print("The module 'synnet' is not installed, please follow the instructions above")

The environment is setup correctly


## Pre-Processing

Now that the conda environment is correctly setup, we can start the preliminary steps to produce the synthesis results.

First, let's import some packages, define some constants.
Make sure they are correct.

In [3]:
from downloader import *
from preprocessor import *
from synthesis import synthesis
import random

project_root = Path("..")  # Path to the project's root folder
cpu_cores = 20  # Number of cores to use for the computation. The greater, the faster
num_samples = 10000  # Number of molecules to randomly pick from the datasets

random.seed(2022)

/home/sabanza/miniconda3/envs/synnet/lib/python3.9/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
19:08:30 rdkit INFO: Enabling RDKit 2021.03.5 jupyter extensions


### Downloads
First, we need to choose the trained model to use. **We can use the model we trained, or the one paper's writers used to get their results.

But for the latter, we need to download it.

In [4]:
original_checkpoints = get_original_checkpoints(project_root)

original_checkpoints is already present, no need to compute it


We download ChEMBL dataset, which was used to evaluate the model.

In [5]:
chembl_smiles = get_chembl_dataset(project_root, num_samples)

ChEMBL is already present, no need to compute it
The number of samples differs from the expected amount. The dataset will be recomputed
chembl_31.sdf.gz is already present, no need to downloade it
chembl_31.sdf is already present, no need to extract it
Loading sdf...  done


Converting sdf to smile: 100%|██████████| 10000/10000 [00:03<00:00, 2977.15mol/s]


Now, we need to retrieve the building blocks. We asked the company to provide them, that way we can correctly reproduce their result

In [6]:
bblocks_raw = get_building_blocks(project_root)

building_blocks is already present, no need to compute it


We also download part of ZINC dataset to introduce an additional testing set in the model analysis part.

In [7]:
zinc_smiles = get_zinc_dataset(project_root, num_samples)

ZINC is already present, no need to compute it
The number of samples differs from the expected amount. The dataset will be recomputed


CABA.txt is already present, no need to downloade it


JJCA.txt is already present, no need to downloade it


IHEA.txt is already present, no need to downloade it


EHAA.txt is already present, no need to downloade it


### Process Building Blocks

### Filter Building Blocks
We pre-process the building blocks to identify applicable reactants for each reaction template. In other words, filter out all building blocks that do not match any reaction template. There is no need to keep them, as they cannot act as reactant.

In a first step, we match all building blocks with each reaction template.
In a second step, we save all matched building blocks and a collection of `Reactions` with their available building blocks.

In [8]:
bblocks, rxn_collection = filter_bblocks(project_root, bblocks_raw, cpu_cores)

filtered building blocks is already present, no need to compute it
rections is already present, no need to compute it


RDKit WARNING: [19:08:49] mapped atoms in the reactants were not mapped in the products.
[19:08:49] mapped atoms in the reactants were not mapped in the products.
  unmapped numbers are: 11 
[19:08:49] mapped atoms in the reactants were not mapped in the products.
  unmapped numbers are: 11 
[19:08:49] mapped atoms in the reactants were not mapped in the products.
  unmapped numbers are: 11 
[19:08:49] mapped atoms in the reactants were not mapped in the products.
  unmapped numbers are: 18 16 
[19:08:49] mapped atoms in the reactants were not mapped in the products.
  unmapped numbers are: 1 14 
[19:08:49] product atom-mapping number 13 not found in reactants.
[19:08:49] mapped atoms in the reactants were not mapped in the products.
  unmapped numbers are: 11 
[19:08:49] product atom-mapping number 10 not found in reactants.
[19:08:49] product atom-mapping number 11 not found in reactants.
[19:08:49] product atom-mapping number 12 not found in reactants.
[19:08:49] product atom-mappin

### Pre-compute embeddings

We use the embedding space for the building blocks a lot. Hence, we pre-compute and store the building blocks.

In [9]:
mol_embedder = compute_embeddings(project_root, bblocks, cpu_cores)

embeddings is already present, no need to compute it


# Synthesis

First, compute synthetic trees for a random sample of 10000 molecules from the original building blocks list.

In [10]:
sample_bblocks = random.sample(bblocks, 10000)

synthesis(sample_bblocks,
          bblocks,
          original_checkpoints,
          rxn_collection,
          mol_embedder,
          project_root / "results" / "bblocks" / "original",
          cpu_cores)

Start.
Start to decode 10000 target molecules.
Starting MP with ncpu=20


RDKit ERROR: [19:08:49] mapped atoms in the reactants were not mapped in the p[19:09:32] Can't kekulize mol.  Unkekulized atoms: 38 39 41


.

RDKit ERROR: 
[19:09:32] Can't kekulize mol.  Unkekulized atoms: 38 39 41



.

...

.

[21:41:13] Can't kekulize mol.  Unkekulized atoms: 8 9 10 11 12 24 25 38 39

RDKit ERROR: [21:41:14] Explicit valence for atom # 8 N, 6, is greater than permitted
attempt to get argmax of an empty sequence


.

[21:41:14] Explicit valence for atom # 8 N, 6, is greater than permitted



Finished decoding.
  Total number of attempted  reconstructions: 10000
  Total number of successful reconstructions: 8714
  recovery_rate=0.8086
  avg_similarity=0.8476673714518967
Saving results to ../results/bblocks/original ...
Completed.


Compute ZINC

In [11]:
synthesis(zinc_smiles,
          bblocks,
          original_checkpoints,
          rxn_collection,
          mol_embedder,
          project_root / "results" / "zinc" / "original",
          cpu_cores)

Start.
Start to decode 10000 target molecules.
Starting MP with ncpu=20
.

RDKit ERROR: [19:08:49] mapped atoms in the reactants were not mapped in the p[22:00:07] Can't kekulize mol.  Unkekulized atoms: 14 15 17
RDKit ERROR: 
[22:00:07] Can't kekulize mol.  Unkekulized atoms: 14 15 17



......

RDKit ERROR: [19:08:49] mapped atoms in the reactants were not mapped in the p[22:00:18] Explicit valence for atom # 7 N, 6, is greater than permitted


.

...

..

RDKit ERROR: [00:32:56] Can't kekulize mol.  Unkekulized atoms: 64 65 67
RDKit ERROR: 


.

[00:32:56] Can't kekulize mol.  Unkekulized atoms: 64 65 67



.....
Finished decoding.
  Total number of attempted  reconstructions: 10000
  Total number of successful reconstructions: 9474
  recovery_rate=0.1898
  avg_similarity=0.6225473952434468
Saving results to ../results/zinc/original ...
Completed.


Compute ChEMBL_SMILES

In [14]:
synthesis(chembl_smiles,
          bblocks,
          original_checkpoints,
          rxn_collection,
          mol_embedder,
          project_root / "results" / "chembl" / "original",
          cpu_cores)

Start.
Start to decode 10000 target molecules.
Starting MP with ncpu=20


RDKit ERROR: [10:08:55] mapped atoms in the reactants were not mapped in the p[13:24:41] Can't kekulize mol.  Unkekulized atoms: 35 36 38
RDKit ERROR: 
[13:24:41] Can't kekulize mol.  Unkekulized atoms: 35 36 38



.

RDKit ERROR: [10:08:55] mapped atoms in the reactants were not mapped in the p[13:24:42] Explicit valence for atom # 7 N, 6, is greater than permitted
attempt to get argmax of an empty sequence


..

...

.....

RDKit ERROR: [16:22:19] Can't kekulize mol.  Unkekulized atoms: 41 42 44
RDKit ERROR: 


.

[16:22:19] Can't kekulize mol.  Unkekulized atoms: 41 42 44



.......
Finished decoding.
  Total number of attempted  reconstructions: 10000
  Total number of successful reconstructions: 9032
  recovery_rate=0.0605
  avg_similarity=0.45337065508090746
Saving results to ../results/chembl/original ...
Completed.
